In [1]:
from sklearn.feature_extraction.text import CountVectorizer
from pandas_summary import DataFrameSummary
import pandas as pd
import numpy as np
import csv
pd.set_option('display.max_columns', 5000)

In [2]:
target_vars = ['DIED']
input_vars_reg_dx = '^DX\d'
input_vars_reg_dxccs = '^DXCCS\d'
input_vars_reg_pr = '^PR\d'
input_vars_reg_prccs = '^PRCCS\d'

In [3]:
fn_pt_trn = pd.read_csv('../../../data/hcup/nis/all_year_combination/train_test.csv', dtype = object, quoting = csv.QUOTE_ALL)

In [4]:
list(fn_pt_trn.YEAR).count('2008')

0

In [7]:
fn_pt_trn.YEAR = fn_pt_trn.YEAR.fillna('2008')

In [8]:
set(fn_pt_trn.YEAR)

{'2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015'}

In [9]:
fn_pt_trn.head()

AGE AGEDAY AGE_NEONATE    AHAID AMONTH APRDRG APRDRG_Risk_Mortality  \
0  49.0    -99         NaN  6860460     10    660                     2   
1  66.0    -99         NaN  6860045      1    660                     2   
2  28.0    -99         NaN  6860028      2    660                     2   
3  39.0    -99         NaN  6860028      3    660                     2   
4  62.0    -99         NaN  6860019      3    660                     2   

  APRDRG_Severity APSDRG APSDRG_Charge_Weight   APSDRG_LOS_Weight  \
0               2   8080              0.69928             0.75759   
1               2   5740              0.66705  0.7702100000000001   
2               2   5740              0.66705  0.7702100000000001   
3               2   5740              0.66705  0.7702100000000001   
4               2   5741   0.9921200000000001             1.08538   

  APSDRG_Mortality_Weight ASOURCE ASOURCEUB92 ASOURCE_X ATYPE AWEEKEND  \
0     0.15292999999999998      -9         NaN       NaN     1        1   
1     0.17789000000000002       2           4         4     2        0   
2     0.17789000000000002       1           7         7     1        1   
3     0.17789000000000002       1           7         7     1        0   
4                  0.6707       1           7         7     1        0   

  BODYSYSTEM1 BODYSYSTEM10 BODYSYSTEM11 BODYSYSTEM12 BODYSYSTEM13  \
0         NaN          NaN          NaN          NaN          NaN   
1         NaN          NaN          NaN          NaN          NaN   
2         NaN          NaN          NaN          NaN          NaN   
3         NaN          NaN          NaN          NaN          NaN   
4         NaN          NaN          NaN          NaN          NaN   

  BODYSYSTEM14 BODYSYSTEM15 BODYSYSTEM16 BODYSYSTEM17 BODYSYSTEM18  \
0          NaN          NaN          NaN          NaN          NaN   
1          NaN          NaN          NaN          NaN          NaN   
2          NaN          NaN          NaN          NaN          NaN   
3          NaN          NaN          NaN          NaN          NaN   
4          NaN          NaN          NaN          NaN          NaN   

  BODYSYSTEM19 BODYSYSTEM2 BODYSYSTEM20 BODYSYSTEM21 BODYSYSTEM22  \
0          NaN         NaN          NaN          NaN          NaN   
1          NaN         NaN          NaN          NaN          NaN   
2          NaN         NaN          NaN          NaN          NaN   
3          NaN         NaN          NaN          NaN          NaN   
4          NaN         NaN          NaN          NaN          NaN   

  BODYSYSTEM23 BODYSYSTEM24 BODYSYSTEM25 BODYSYSTEM26 BODYSYSTEM27  \
0          NaN          NaN          NaN          NaN          NaN   
1          NaN          NaN          NaN          NaN          NaN   
2          NaN          NaN          NaN          NaN          NaN   
3          NaN          NaN          NaN          NaN          NaN   
4          NaN          NaN          NaN          NaN          NaN   

  BODYSYSTEM28 BODYSYSTEM29 BODYSYSTEM3 BODYSYSTEM30 BODYSYSTEM4 BODYSYSTEM5  \
0          NaN          NaN         NaN          NaN         NaN         NaN   
1          NaN          NaN         NaN          NaN         NaN         NaN   
2          NaN          NaN         NaN          NaN         NaN         NaN   
3          NaN          NaN         NaN          NaN         NaN         NaN   
4          NaN          NaN         NaN          NaN         NaN         NaN   

  BODYSYSTEM6 BODYSYSTEM7 BODYSYSTEM8 BODYSYSTEM9 CHRON1 CHRON10 CHRON11  \
0         NaN         NaN         NaN         NaN      1     -99     -99   
1         NaN         NaN         NaN         NaN      1     -99     -99   
2         NaN         NaN         NaN         NaN      1     -99     -99   
3         NaN         NaN         NaN         NaN      1     -99     -99   
4         NaN         NaN         NaN         NaN      1     -99     -99   

  CHRON12 CHRON13 CHRON14 CHRON15 CHRON16 CHRON17 CHRON18 CHRON19 CHRON2  \
0     -

## Create Charlson's Comorbidity Index

In [13]:
# Myocardial infarction
icd9_mi = ['410', '412']
# Congestive heart failure
icd9_chf = ['428']
# Peripheral vascular disease
icd9_pvd = ['4439', '441', '7854', 'V434']
# Cerebrovascular disease
icd9_cd = ['430', '438']
# Dementia
icd9_dem = ['290']
# Chronic pulmonary disease
icd9_cpd = ['490', '491', '492', '493', '494', '495', '496', '497', '498', '499', '500', '501', '502', '503', 
            '504', '505', '5064']
# Rheumatic disease
icd9_rd = ['7100', '7101', '7104', '7140', '7141', '7142', '71481', '7125']
# Peptic ulcer disease
icd9_pud = ['531', '532', '533', '534']
# Mild liver disease
icd9_mld = ['5712', '5714', '5715', '5716']
# Diabetes without chronic complication
icd9_dw0cc = ['2500', '2501', '2502', '2503', '2507']
# Diabetes with chronic complication
icd9_dw1cc = ['2504', '2505', '2506']
# Hemiplegia or paraplegia
icd9_hop = ['3441', '342']
# Renal disease
icd9_rd = ['582', '5830', '5831', '5832', '5833', '5834', '5835', '5836', '5837', '585', '586', '588']
# Any malignancy
icd9_am = [str(x) for x in list(range(140,173))] + [str(x) for x in list(range(174,195))] + ['1958'] + [str(x) for x in list(range(200,209))]
# Moderate or severe liver disease
icd9_msld = ['4560', '4561', '45620', '45621', '5722', '5723', '5724', '5725', '5726', '5727', '5728']
# Metastatic solid tumor
icd9_mst = ['196', '197', '198', '1990', '1991']
# AIDS/HIV
icd9_hiv = ['042', '043', '044']

In [15]:
dx_reg = '^DX\d'
ci_reg = '^CHRON\d'
def add_cci(row):
#    print(row.row_id)
    if row.row_id%10000 == 0:
        print(row.row_id/157295)
    point1 = icd9_mi + icd9_chf + icd9_pvd + icd9_cd + icd9_dem + icd9_cpd + icd9_rd + icd9_pud + icd9_mld + icd9_dw0cc
    point2 = icd9_dw1cc + icd9_hop + icd9_rd + icd9_am
    point3 = icd9_msld
    point6 = icd9_mst + icd9_hiv
    point = 0
    for icd9, cci in zip(row.filter(regex = dx_reg), row.filter(regex = ci_reg)):
        if pd.isnull(icd9) or cci == '0':
            continue
        else:
            for code in point1 + point2 + point3 + point6:
                if icd9.startswith(code): 
                    if code in point1:
                        point += 1
                    elif code in point2:
                        point += 2
                    elif code in point3:
                        point += 3
                    elif code in point6:
                        point += 6

    return point

In [19]:
fn_pt_trn['row_id'] = list(fn_pt_trn.index)

In [20]:
fn_pt_trn['CCI'] = fn_pt_trn.apply(lambda row: add_cci(row),axis=1)

0.0
0.06357481165962046
0.12714962331924093
0.19072443497886138
0.25429924663848186
0.3178740582981023
0.38144886995772276
0.44502368161734324
0.5085984932769637
0.5721733049365841
0.6357481165962046
0.6993229282558251
0.7628977399154455
0.8264725515750659
0.8900473632346865
0.9536221748943069


In [5]:
len(fn_pt_trn)

126013

In [6]:
target_df = fn_pt_trn['DIED']

In [38]:
#input_df_standard = fn_pt_standard.filter(regex = input_vars_reg_dx)
#input_df_standard.fillna(value = '-1', inplace = True)

## One-hot encoding for APRDRG

In [7]:
col_names = ['APRDRG', 'APRDRG_Risk_Mortality', 'APRDRG_Severity']

In [8]:
def APRDRG_ALL(row):
    corpus = ''
    for col in col_names:
        corpus += '_' + str(row[col])
    return corpus.strip()

In [9]:
fn_pt_trn['APRDRG_ALL'] = fn_pt_trn.apply(lambda row: APRDRG_ALL(row), axis = 1)

In [10]:
fn_pt_trn.head()

AGE AGEDAY AGE_NEONATE    AHAID AMONTH APRDRG APRDRG_Risk_Mortality  \
0  49.0    -99         NaN  6860460     10    660                     2   
1  66.0    -99         NaN  6860045      1    660                     2   
2  28.0    -99         NaN  6860028      2    660                     2   
3  39.0    -99         NaN  6860028      3    660                     2   
4  62.0    -99         NaN  6860019      3    660                     2   

  APRDRG_Severity APSDRG APSDRG_Charge_Weight   APSDRG_LOS_Weight  \
0               2   8080              0.69928             0.75759   
1               2   5740              0.66705  0.7702100000000001   
2               2   5740              0.66705  0.7702100000000001   
3               2   5740              0.66705  0.7702100000000001   
4               2   5741   0.9921200000000001             1.08538   

  APSDRG_Mortality_Weight ASOURCE ASOURCEUB92 ASOURCE_X ATYPE AWEEKEND  \
0     0.15292999999999998      -9         NaN       NaN     1        1   
1     0.17789000000000002       2           4         4     2        0   
2     0.17789000000000002       1           7         7     1        1   
3     0.17789000000000002       1           7         7     1        0   
4                  0.6707       1           7         7     1        0   

  BODYSYSTEM1 BODYSYSTEM10 BODYSYSTEM11 BODYSYSTEM12 BODYSYSTEM13  \
0         NaN          NaN          NaN          NaN          NaN   
1         NaN          NaN          NaN          NaN          NaN   
2         NaN          NaN          NaN          NaN          NaN   
3         NaN          NaN          NaN          NaN          NaN   
4         NaN          NaN          NaN          NaN          NaN   

  BODYSYSTEM14 BODYSYSTEM15 BODYSYSTEM16 BODYSYSTEM17 BODYSYSTEM18  \
0          NaN          NaN          NaN          NaN          NaN   
1          NaN          NaN          NaN          NaN          NaN   
2          NaN          NaN          NaN          NaN          NaN   
3          NaN          NaN          NaN          NaN          NaN   
4          NaN          NaN          NaN          NaN          NaN   

  BODYSYSTEM19 BODYSYSTEM2 BODYSYSTEM20 BODYSYSTEM21 BODYSYSTEM22  \
0          NaN         NaN          NaN          NaN          NaN   
1          NaN         NaN          NaN          NaN          NaN   
2          NaN         NaN          NaN          NaN          NaN   
3          NaN         NaN          NaN          NaN          NaN   
4          NaN         NaN          NaN          NaN          NaN   

  BODYSYSTEM23 BODYSYSTEM24 BODYSYSTEM25 BODYSYSTEM26 BODYSYSTEM27  \
0          NaN          NaN          NaN          NaN          NaN   
1          NaN          NaN          NaN          NaN          NaN   
2          NaN          NaN          NaN          NaN          NaN   
3          NaN          NaN          NaN          NaN          NaN   
4          NaN          NaN          NaN          NaN          NaN   

  BODYSYSTEM28 BODYSYSTEM29 BODYSYSTEM3 BODYSYSTEM30 BODYSYSTEM4 BODYSYSTEM5  \
0          NaN          NaN         NaN          NaN         NaN         NaN   
1          NaN          NaN         NaN          NaN         NaN         NaN   
2          NaN          NaN         NaN          NaN         NaN         NaN   
3          NaN          NaN         NaN          NaN         NaN         NaN   
4          NaN          NaN         NaN          NaN         NaN         NaN   

  BODYSYSTEM6 BODYSYSTEM7 BODYSYSTEM8 BODYSYSTEM9 CHRON1 CHRON10 CHRON11  \
0         NaN         NaN         NaN         NaN      1     -99     -99   
1         NaN         NaN         NaN         NaN      1     -99     -99   
2         NaN         NaN         NaN         NaN      1     -99     -99   
3         NaN         NaN         NaN         NaN      1     -99     -99   
4         NaN         NaN         NaN         NaN      1     -99     -99   

  CHRON12 CHRON13 CHRON14 CHRON15 CHRON16 CHRON17 CHRON18 CHRON19 CHRON2  \
0     -

In [11]:
unique_values = list(set(fn_pt_trn['APRDRG_ALL']))

In [12]:
from sklearn.feature_extraction.text import CountVectorizer
vectorizer = CountVectorizer(token_pattern = '(\S+)', vocabulary = unique_values, binary = True)

In [13]:
corpus = list(fn_pt_trn['APRDRG_ALL'])

In [14]:
transformer = vectorizer.fit(corpus)

In [15]:
names = vectorizer.get_feature_names()

In [16]:
X_trn = transformer.transform(corpus)

In [17]:
aprdrg_df = pd.DataFrame()

In [18]:
X_trn_dense = X_trn.todense()

In [19]:
len(unique_values)

1510

In [20]:
for i, var in enumerate(names):
    if(i%100 == 0):
        print(i/2183)
    aprdrg_df['APRDRG_' + var] = np.squeeze(np.array(X_trn_dense[:,i]))

0.0
0.04580852038479157
0.09161704076958314
0.1374255611543747
0.1832340815391663
0.22904260192395787
0.2748511223087494
0.320659642693541
0.3664681630783326
0.4122766834631241
0.45808520384791573
0.5038937242327073
0.5497022446174988
0.5955107650022904
0.641319285387082
0.6871278057718736


In [21]:
aprdrg_df.head()

APRDRG__344_2_4  APRDRG__41_2_2  APRDRG__53_2_2  APRDRG__249_4_3  \
0                0               0               0                0   
1                0               0               0                0   
2                0               0               0                0   
3                0               0               0                0   
4                0               0               0                0   

   APRDRG__484_3_4  APRDRG__721_2_4  APRDRG__384_1_2  APRDRG__42_2_3  \
0                0                0                0               0   
1                0                0                0               0   
2                0                0                0               0   
3                0                0                0               0   
4                0                0                0               0   

   APRDRG__844_2_2  APRDRG__113_2_2  APRDRG__247_1_3  APRDRG__198_2_3  \
0                0                0                0                0   
1                0                0                0                0   
2                0                0                0                0   
3                0                0                0                0   
4                0                0                0                0   

   APRDRG__860_2_3  APRDRG__443_1_3  APRDRG__651_4_4  APRDRG__753_2_3  \
0                0                0                0                0   
1                0                0                0                0   
2                0                0                0                0   
3                0                0                0                0   
4                0                0                0                0   

   APRDRG__650_4_4  APRDRG__249_1_4  APRDRG__3_2_4  APRDRG__190_3_3  \
0                0                0              0                0   
1                0                0              0                0   
2                0                0              0                0   
3                0                0              0                0   
4                0                0              0                0   

   APRDRG__225_2_2  APRDRG__173_2_2  APRDRG__661_2_2  APRDRG__140_2_3  \
0                0                0                0                0   
1                0                0                0                0   
2                0                0                0                0   
3                0                0                0                0   
4                0                0                0                0   

   APRDRG__751_4_4  APRDRG__98_3_3  APRDRG__201_2_1  APRDRG__139_4_3  \
0                0               0                0                0   
1                0               0                0                0   
2                0               0                0                0   
3                0               0                0                0   
4                0               0                0                0   

   APRDRG__309_3_3  APRDRG__204_2_3  APRDRG__466_2_4  APRDRG__44_3_4  \
0                0                0                0               0   
1                0                0                0               0   
2                0                0                0               0   
3                0                0                0               0   
4                0                0                0               0   

   APRDRG__343_2_3  APRDRG__133_3_4  APRDRG__650_1_3  APRDRG__284_4_4  \
0                0                0                0                0   
1                0                0                0                0   
2                0                0                0                0   
3                0                0                0                0   
4                0                0                0                0   

   APRDRG__53_1_2  APRDRG__301_1_2  APRDRG__680_3_3  APRDRG__141_3_3  \
0               0     

In [22]:
path_aprdrg_df = '../../../data/hcup/nis/all_year_combination/aprdrg.pickle'

In [23]:
pd.concat([target_df, aprdrg_df], axis = 1).to_pickle(path_aprdrg_df)

## One-Hot Encoding for DX

In [24]:
input_df = fn_pt_trn.filter(regex = input_vars_reg_dx)

In [25]:
input_df.fillna(value = '-1', inplace = True)

/apps/python3/3.6.5/lib/python3.6/site-packages/pandas/core/frame.py:3790: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  downcast=downcast, **kwargs)


In [26]:
input_df.head()

DX1 DX10 DX11 DX12 DX13 DX14 DX15 DX16 DX17 DX18 DX19   DX2 DX20 DX21  \
0  28800   -1   -1   -1   -1   -1   -1   -1   -1   -1   -1  7806   -1   -1   
1  28800   -1   -1   -1   -1   -1   -1   -1   -1   -1   -1  7806   -1   -1   
2  28800   -1   -1   -1   -1   -1   -1   -1   -1   -1   -1  7806   -1   -1   
3  28800   -1   -1   -1   -1   -1   -1   -1   -1   -1   -1  7806   -1   -1   
4  28809   -1   -1   -1   -1   -1   -1   -1   -1   -1   -1  7806   -1   -1   

  DX22 DX23 DX24 DX25 DX26 DX27 DX28 DX29    DX3 DX30    DX4    DX5    DX6  \
0   -1   -1   -1   -1   -1   -1   -1   -1   1749   -1  V4571  05419  07070   
1   -1   -1   -1   -1   -1   -1   -1   -1   1749   -1  05411   2859   2841   
2   -1   -1   -1   -1   -1   -1   -1   -1   1869   -1   2449    462   2768   
3   -1   -1   -1   -1   -1   -1   -1   -1   1749   -1  V1041   2859     -1   
4   -1   -1   -1   -1   -1   -1   -1   -1  20300   -1   2841   7241   9051   

     DX7    DX8    DX9  
0  V1508   3051  V4573  
1  56400   3004  71690  
2  V5869  V4577     -1  
3     -1     -1     -1  
4  28989   4019   2749

In [27]:
col_names = list(input_df.columns)

In [28]:
unique_values = []
for col in input_df:
    unique_values += list(input_df[col].unique())

In [29]:
unique_values = list(set(unique_values))

In [30]:
len(unique_values)

6066

In [31]:
cleaned_unique_values = []
for i in unique_values:
    if i >= '0':
        cleaned_unique_values.append(i)

In [32]:
def corpus_generator(row):
    corpus = ''
    for col in col_names:
        corpus += ' ' + row[col]
    return corpus.strip()

In [33]:
input_df['DX_corpus'] = input_df.apply(lambda row: corpus_generator(row), axis = 1)

/apps/python3/3.6.5/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [34]:
input_df['DX_corpus'].head()

0    28800 -1 -1 -1 -1 -1 -1 -1 -1 -1 -1 7806 -1 -1...
1    28800 -1 -1 -1 -1 -1 -1 -1 -1 -1 -1 7806 -1 -1...
2    28800 -1 -1 -1 -1 -1 -1 -1 -1 -1 -1 7806 -1 -1...
3    28800 -1 -1 -1 -1 -1 -1 -1 -1 -1 -1 7806 -1 -1...
4    28809 -1 -1 -1 -1 -1 -1 -1 -1 -1 -1 7806 -1 -1...
Name: DX_corpus, dtype: object

In [35]:
vectorizer = CountVectorizer(token_pattern = '(\S+)', vocabulary = cleaned_unique_values, binary = True)

In [36]:
corpus = list(input_df['DX_corpus'])

In [37]:
transformer = vectorizer.fit(corpus)

In [38]:
names = vectorizer.get_feature_names()

In [39]:
X_trn = transformer.transform(corpus)

In [40]:
X_trn.shape

(126013, 6065)

### Convert transformed DX variables to DataFrame

In [41]:
dx_df = pd.DataFrame()

In [42]:
len(names)

6065

In [43]:
X_trn_dense = X_trn.todense()

In [44]:
for i, var in enumerate(names):
    if(i%100 == 0):
        print(i/6684)
    dx_df['DX_' + var] = np.squeeze(np.array(X_trn_dense[:,i]))

0.0
0.014961101137043686
0.029922202274087373
0.04488330341113106
0.059844404548174746
0.07480550568521843
0.08976660682226212
0.1047277079593058
0.11968880909634949
0.13464991023339318
0.14961101137043686
0.16457211250748055
0.17953321364452424
0.19449431478156792
0.2094554159186116
0.2244165170556553
0.23937761819269898
0.25433871932974267
0.26929982046678635
0.28426092160383004
0.2992220227408737
0.3141831238779174
0.3291442250149611
0.3441053261520048
0.3590664272890485
0.37402752842609216
0.38898862956313585
0.40394973070017953
0.4189108318372232
0.4338719329742669
0.4488330341113106
0.4637941352483543
0.47875523638539796
0.49371633752244165
0.5086774386594853
0.5236385397965291
0.5385996409335727
0.5535607420706165
0.5685218432076601
0.5834829443447038
0.5984440454817475
0.6134051466187912
0.6283662477558348
0.6433273488928786
0.6582884500299222
0.6732495511669659
0.6882106523040096
0.7031717534410533
0.718132854578097
0.7330939557151407
0.7480550568521843
0.7630161579892281
0.77

In [45]:
dx_df.head()

DX_4730  DX_70711  DX_36132  DX_94301  DX_36844  DX_4293  DX_2809  DX_V854  \
0        0         0         0         0         0        0        0        0   
1        0         0         0         0         0        0        0        0   
2        0         0         0         0         0        0        0        0   
3        0         0         0         0         0        0        0        0   
4        0         0         0         0         0        0        0        0   

   DX_64821  DX_V118  DX_53540  DX_7804  DX_37271  DX_4802  DX_5758  DX_3343  \
0         0        0         0        0         0        0        0        0   
1         0        0         0        0         0        0        0        0   
2         0        0         0        0         0        0        0        0   
3         0        0         0        0         0        0        0        0   
4         0        0         0        0         0        0        0        0   

   DX_41405  DX_5690  DX_1451  DX_28269  DX_2513  DX_38910  DX_V157  DX_29181  \
0         0        0        0         0        0         0        0         0   
1         0        0        0         0        0         0        0         0   
2         0        0        0         0        0         0        0         0   
3         0        0        0         0        0         0        0         0   
4         0        0        0         0        0         0        0         0   

   DX_4413  DX_60490  DX_34500  DX_23770  DX_20501  DX_0416  DX_V600  \
0        0         0         0         0         0        0        0   
1        0         0         0         0         0        0        0   
2        0         0         0         0         0        0        0   
3        0         0         0         0         0        0        0   
4        0         0         0         0         0        0        0   

   DX_44020  DX_87340  DX_V4987  DX_1410  DX_1118  DX_5966  DX_65951  DX_2382  \
0         0         0         0        0        0        0         0        0   
1         0         0         0        0        0        0         0        0   
2         0         0         0        0        0        0         0        0   
3         0         0         0        0        0        0         0        0   
4         0         0         0        0        0        0         0        0   

   DX_2781  DX_8761  DX_30989  DX_74760  DX_53013  DX_V4459  DX_68102  \
0        0        0         0         0         0         0         0   
1        0        0         0         0         0         0         0   
2        0        0         0         0         0         0         0   
3        0        0         0         0         0         0         0   
4        0        0         0         0         0         0         0   

   DX_4321  DX_4142  DX_28800  DX_37500  DX_V4283  DX_V1047  DX_V166  DX_9630  \
0        0        0         1         0         0         0        0        0   
1        0        0         1         0         0         0        0        0   
2        0        0         1         0         0         0        0        0   
3        0        0         1         0         0         0        0        0   
4        0        0         0         0         0         0        0        0   

   DX_5225  DX_1521  DX_41092  DX_67424  DX_1261  DX_1619  DX_95901  DX_6189  \
0        0        0         0         0        0        0         0        0   
1        0        0         0         0        0        0         0        0   
2        0        0         0         0        0        0         0        0   
3        0        0         0         0        0        0         0        0   
4        0        0         0         0        0        0         0        0   

   DX_1542  DX_6228  DX_1749  DX_81344  DX_41041  DX_94100  DX_7010  DX_20411  \
0        0        0        1         0         0         0        0         0   
1        0        0        1         0         0         0 

In [48]:
# Remove case-defining variables, but keep 288.01 as a predictor, since it is pre-date to the admission

dx_df = dx_df.drop(columns = 'DX_28800')
dx_df = dx_df.drop(columns = 'DX_28802')
dx_df = dx_df.drop(columns = 'DX_28803')
dx_df = dx_df.drop(columns = 'DX_28804')
dx_df = dx_df.drop(columns = 'DX_28809')

KeyError: "['DX_28800'] not found in axis"

In [49]:
dx_df = dx_df.loc[:, ~dx_df.columns.str.startswith('DX_2841')]
dx_df = dx_df.loc[:, ~dx_df.columns.str.startswith('DX_1125')]

In [50]:
len(dx_df.columns)

6055

In [51]:
path_dx_df = '../../../data/hcup/nis/all_year_combination/dx.pickle'

In [52]:
pd.concat([target_df, dx_df], axis = 1).to_pickle(path_dx_df)

## One-hot Encoding for DXCCS

In [53]:
input_df = fn_pt_trn.filter(regex = input_vars_reg_dxccs)
input_df.fillna(value = '-1', inplace = True)
col_names = list(input_df.columns)
unique_values = []
for col in input_df:
    unique_values += list(input_df[col].unique())

/apps/python3/3.6.5/lib/python3.6/site-packages/pandas/core/frame.py:3790: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  downcast=downcast, **kwargs)


In [54]:
unique_values = list(set(unique_values))
len(unique_values)

258

In [55]:
cleaned_unique_values = []
for i in unique_values:
    if i >= '0':
        cleaned_unique_values.append(i)

In [56]:
input_df['DXCCS_corpus'] = input_df.apply(lambda row: corpus_generator(row), axis = 1)
vectorizer = CountVectorizer(token_pattern = '(\S+)', vocabulary = cleaned_unique_values, binary = True)
corpus = list(input_df['DXCCS_corpus'])
transformer = vectorizer.fit(corpus)
names = vectorizer.get_feature_names()
X_trn = transformer.transform(corpus)

/apps/python3/3.6.5/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [57]:
dxccs_df = pd.DataFrame()
X_trn_dense = X_trn.todense()

In [58]:
for i, var in enumerate(names):
    if(i%100 == 0):
        print(i/6684)
    dxccs_df['DXCCS_' + var] = np.squeeze(np.array(X_trn_dense[:,i]))

0.0
0.014961101137043686
0.029922202274087373


In [59]:
path_dxccs_df = '../../../data/hcup/nis/all_year_combination/dxccs.pickle'

In [60]:
pd.concat([target_df, dxccs_df], axis = 1).to_pickle(path_dxccs_df)

## One-hot encoding for PR

In [61]:
input_df = fn_pt_trn.filter(regex = input_vars_reg_pr)
input_df.fillna(value = '-1', inplace = True)
col_names = list(input_df.columns)
unique_values = []
for col in input_df:
    unique_values += list(input_df[col].unique())

/apps/python3/3.6.5/lib/python3.6/site-packages/pandas/core/frame.py:3790: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  downcast=downcast, **kwargs)


In [62]:
unique_values = list(set(unique_values))
len(unique_values)

1593

In [63]:
cleaned_unique_values = []
for i in unique_values:
    if i >= '0':
        cleaned_unique_values.append(i)

In [64]:
input_df['PR_corpus'] = input_df.apply(lambda row: corpus_generator(row), axis = 1)
vectorizer = CountVectorizer(token_pattern = '(\S+)', vocabulary = cleaned_unique_values, binary = True)
corpus = list(input_df['PR_corpus'])
transformer = vectorizer.fit(corpus)
names = vectorizer.get_feature_names()
X_trn = transformer.transform(corpus)

/apps/python3/3.6.5/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [65]:
pr_df = pd.DataFrame()
X_trn_dense = X_trn.todense()

In [66]:
for i, var in enumerate(names):
    if(i%100 == 0):
        print(i/6684)
    pr_df['PR_' + var] = np.squeeze(np.array(X_trn_dense[:,i]))

0.0
0.014961101137043686
0.029922202274087373
0.04488330341113106
0.059844404548174746
0.07480550568521843
0.08976660682226212
0.1047277079593058
0.11968880909634949
0.13464991023339318
0.14961101137043686
0.16457211250748055
0.17953321364452424
0.19449431478156792
0.2094554159186116
0.2244165170556553


In [67]:
path_pr_df = '../../../data/hcup/nis/all_year_combination/pr.pickle'

In [68]:
pd.concat([target_df, pr_df], axis = 1).to_pickle(path_pr_df)

## One-hot encoding for PRCCS

In [69]:
input_df = fn_pt_trn.filter(regex = input_vars_reg_prccs)
input_df.fillna(value = '-1', inplace = True)
col_names = list(input_df.columns)
unique_values = []
for col in input_df:
    unique_values += list(input_df[col].unique())

/apps/python3/3.6.5/lib/python3.6/site-packages/pandas/core/frame.py:3790: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  downcast=downcast, **kwargs)


In [70]:
unique_values = list(set(unique_values))
len(unique_values)

218

In [71]:
cleaned_unique_values = []
for i in unique_values:
    if i >= '0':
        cleaned_unique_values.append(i)

In [72]:
input_df['PRCCS_corpus'] = input_df.apply(lambda row: corpus_generator(row), axis = 1)
vectorizer = CountVectorizer(token_pattern = '(\S+)', vocabulary = cleaned_unique_values, binary = True)
corpus = list(input_df['PRCCS_corpus'])
transformer = vectorizer.fit(corpus)
names = vectorizer.get_feature_names()
X_trn = transformer.transform(corpus)

/apps/python3/3.6.5/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [73]:
prccs_df = pd.DataFrame()
X_trn_dense = X_trn.todense()

In [74]:
for i, var in enumerate(names):
    if(i%100 == 0):
        print(i/6684)
    prccs_df['PRCCS_' + var] = np.squeeze(np.array(X_trn_dense[:,i]))

0.0
0.014961101137043686
0.029922202274087373


In [75]:
path_prccs_df = '../../../data/hcup/nis/all_year_combination/prccs.pickle'

In [76]:
pd.concat([target_df, prccs_df], axis = 1).to_pickle(path_prccs_df)

## One-hot Encoding for PCLASS

In [77]:
input_vars_reg_pclass = '^PCLASS\d'

In [78]:
input_df_pclass = fn_pt_trn.filter(regex = input_vars_reg_pclass)

In [79]:
pclass1 = []
pclass2 = []
pclass3 = []
pclass4 = []

In [80]:
for i in range(len(input_df_pclass)):
    if '1' in list(input_df_pclass.iloc[i]):
        pclass1.append(1)
    else:
        pclass1.append(0)
    if '2' in list(input_df_pclass.iloc[i]):
        pclass2.append(1)
    else:
        pclass2.append(0)
    if '3' in list(input_df_pclass.iloc[i]):
        pclass3.append(1)
    else:
        pclass3.append(0)
    if '4' in list(input_df_pclass.iloc[i]):
        pclass4.append(1)
    else:
        pclass4.append(0)

In [81]:
pclass_df = pd.DataFrame()

In [82]:
pclass_df['PCLASS_1'] = pclass1
pclass_df['PCLASS_2'] = pclass2
pclass_df['PCLASS_3'] = pclass3
pclass_df['PCLASS_4'] = pclass4

In [83]:
pclass_df.head()

PCLASS_1  PCLASS_2  PCLASS_3  PCLASS_4
0         0         1         0         0
1         0         0         0         0
2         0         0         0         0
3         0         0         0         0
4         0         1         0         0

In [84]:
path_pclass_df = '../../../data/hcup/nis/all_year_combination/pclass.pickle'

In [85]:
pd.concat([target_df, pclass_df], axis = 1).to_pickle(path_pclass_df)

## Construct other related variables

In [86]:
dqtr_dummy_df = pd.get_dummies(fn_pt_trn['DQTR'], prefix = 'DQTR')
amonth_dummy_df = pd.get_dummies(fn_pt_trn['AMONTH'], prefix = 'AMONTH')
hosp_region_dummy_df = pd.get_dummies(fn_pt_trn['HOSP_REGION'], prefix = 'HOSP_REGION')
h_contrl_dummy_df = pd.get_dummies(fn_pt_trn['H_CONTRL'], prefix = 'H_CONTRL')
pay1_dummy_df = pd.get_dummies(fn_pt_trn['PAY1'], prefix = 'PAY1')
race_dummy_df = pd.get_dummies(fn_pt_trn['RACE'], prefix = 'RACE')
zipinc_qrtl_dummy_df = pd.get_dummies(fn_pt_trn['ZIPINC_QRTL'], prefix = 'ZIPINC_QRTL')
hcup_ed_dummy_df = pd.get_dummies(fn_pt_trn['HCUP_ED'], prefix = 'HCUP_ED')
hosp_locteach_dummy_df = pd.get_dummies(fn_pt_trn['HOSP_LOCTEACH'], prefix = 'HOSP_LOCTEACH')

In [87]:
fn_pt_trn = pd.concat([fn_pt_trn, dqtr_dummy_df, amonth_dummy_df, hosp_region_dummy_df, h_contrl_dummy_df, 
                       pay1_dummy_df, race_dummy_df, zipinc_qrtl_dummy_df, hcup_ed_dummy_df, 
                       hosp_locteach_dummy_df], axis = 1)

In [88]:
cm_vars = ['CM_LYMPH', 'CM_LIVER', 'CM_PARA', 'CM_RENLFAIL', 'CM_AIDS', 'CM_ALCOHOL', 'CM_ANEMDEF',
            'CM_ARTH', 'CM_BLDLOSS', 'CM_CHF', 'CM_CHRNLUNG', 'CM_COAG', 'CM_DEPRESS', 'CM_DM', 'CM_DMCX', 'CM_DRUG',
            'CM_HTN_C', 'CM_HYPOTHY', 'CM_LYTES', 'CM_METS', 'CM_OBESE', 'CM_NEURO', 'CM_PERIVASC', 'CM_PSYCH',
            'CM_PULMCIRC', 'CM_ULCER', 'CM_VALVE', 'CM_WGHTLOSS', 'CM_TUMOR', 'CCI']

amonth_vars = ['AMONTH_1', 'AMONTH_2', 'AMONTH_3', 'AMONTH_4', 'AMONTH_5', 'AMONTH_6', 'AMONTH_7',
               'AMONTH_8', 'AMONTH_9', 'AMONTH_10', 'AMONTH_11', 'AMONTH_12']

dqtr_vars = ['DQTR_1', 'DQTR_2', 'DQTR_3', 'DQTR_4']

hosp_region_vars = ['HOSP_REGION_1', 'HOSP_REGION_2', 'HOSP_REGION_3', 'HOSP_REGION_4']

# for former years, if don't have H_CONTRL, change it to HOSP_CONTROL
h_contrl_vars = ['H_CONTRL_1', 'H_CONTRL_2', 'H_CONTRL_3']

pay1_vars = ['PAY1_1', 'PAY1_2', 'PAY1_3', 'PAY1_4', 'PAY1_5', 'PAY1_6']

race_vars = ['RACE_1', 'RACE_2', 'RACE_3', 'RACE_4', 'RACE_5', 'RACE_6']

bin_vars = ['AWEEKEND', 'ELECTIVE', 'FEMALE', 'ORPROC']

zipinc_qrtl_vars = ['ZIPINC_QRTL_1', 'ZIPINC_QRTL_2', 'ZIPINC_QRTL_3', 'ZIPINC_QRTL_4']

hcup_ed_vars = ['HCUP_ED_0', 'HCUP_ED_1', 'HCUP_ED_2', 'HCUP_ED_3', 'HCUP_ED_4']

hosp_locteach_vars = ['HOSP_LOCTEACH_1', 'HOSP_LOCTEACH_2', 'HOSP_LOCTEACH_3']

num_vars = ['HOSP_BEDSIZE', 'N_DISC_U', 'N_HOSP_U', 'AGE', 'TOTCHG', 'NDX', 'NPR', 'TOTAL_DISC', 'NCHRONIC',
                'NECODE', 'S_DISC_U', 'S_HOSP_U', 'PL_NCHS']

dummy = ['MDC', 'DRG']

keys = ['KEY_NIS', 'KEY']

cat_vars = dummy + cm_vars + amonth_vars + dqtr_vars + hosp_region_vars + h_contrl_vars + pay1_vars + race_vars + bin_vars + zipinc_qrtl_vars + hcup_ed_vars + hosp_locteach_vars

names = cat_vars + num_vars + keys

In [89]:
input_df_other = fn_pt_trn[names]

In [90]:
input_df_other.head()

MDC  DRG CM_LYMPH CM_LIVER CM_PARA CM_RENLFAIL CM_AIDS CM_ALCOHOL  \
0  16  810        0        0       0           0       0          0   
1  16  574        0        0       0           0       0          0   
2  16  574        0        0       0           0       0          0   
3  16  574        0        0       0           0       0          0   
4  16  574        1        0       0           0       0          0   

  CM_ANEMDEF CM_ARTH CM_BLDLOSS CM_CHF CM_CHRNLUNG CM_COAG CM_DEPRESS CM_DM  \
0          0       0          0      0           0       0          0     0   
1          0       0          0      0           0       0          1     0   
2          0       0          0      0           0       0          0     0   
3          0       0          0      0           0       0          0     0   
4          0       0          0      0           0       0          0     0   

  CM_DMCX CM_DRUG CM_HTN_C CM_HYPOTHY CM_LYTES CM_METS CM_OBESE CM_NEURO  \
0       0       0        0          0        0       0        0        0   
1       0       0        0          0        0       0        0        0   
2       0       0        0          1        1       0        0        0   
3       0       0        0          0        0       0        0        0   
4       0       0        1          0        0       0        0        0   

  CM_PERIVASC CM_PSYCH CM_PULMCIRC CM_ULCER CM_VALVE CM_WGHTLOSS CM_TUMOR CCI  \
0           0        0           0        0        0           0        1   2   
1           0        0           0        0        0           0        1   2   
2           0        0           0        0        0           0        1   2   
3           0        0           0        0        0           0        1   2   
4           0        0           0        0        0           0        0   2   

   AMONTH_1  AMONTH_2  AMONTH_3  AMONTH_4  AMONTH_5  AMONTH_6  AMONTH_7  \
0         0         0         0         0         0         0         0   
1         1         0         0         0         0         0         0   
2         0         1         0         0         0         0         0   
3         0         0         1         0         0         0         0   
4         0         0         1         0         0         0         0   

   AMONTH_8  AMONTH_9  AMONTH_10  AMONTH_11  AMONTH_12  DQTR_1  DQTR_2  \
0         0         0          1          0          0       0       0   
1         0         0          0          0          0       1       0   
2         0         0          0          0          0       1       0   
3         0         0          0          0          0       1       0   
4         0         0          0          0          0       1       0   

   DQTR_3  DQTR_4  HOSP_REGION_1  HOSP_REGION_2  HOSP_REGION_3  HOSP_REGION_4  \
0       0       1              0              0              0              1   
1       0       0              0              0              0              1   
2       0       0              0              0              0              1   
3       0       0              0              0              0              1   
4       0       0              0              0              0              1   

   H_CONTRL_1  H_CONTRL_2  H_CONTRL_3  PAY1_1  PAY1_2  PAY1_3  PAY1_4  PAY1_5  \
0           0           1           0       0       0       1       0       0   
1           0           0           0       1       0       0       0       0   
2           0           1           0       0       0       1       0       0   
3           0           1           0       0       0       1       0       0   
4           0           0           0       1       0       0       0       0   

   PAY1_6  RACE_1  RACE_2  RACE_3  RACE_4  RACE_5  RACE_6 AWEEKEND ELECTIVE  \
0       0       1       0       0       0       0       0        1        0   
1       0       1       0       0       0       0       0        0        0   
2       0       1       0       0       0       0

## One-hot encoding MDC

In [91]:
df_mdc = pd.get_dummies(input_df_other['MDC'], prefix = 'MDC')

In [92]:
df_mdc = df_mdc.drop(columns = 'MDC_-9')
# df_mdc = df_mdc.drop(columns = 'MDC_-1')

KeyError: "['MDC_-1'] not found in axis"

In [93]:
df_mdc.head()

MDC_0  MDC_1  MDC_10  MDC_11  MDC_12  MDC_13  MDC_14  MDC_16  MDC_17  \
0      0      0       0       0       0       0       0       1       0   
1      0      0       0       0       0       0       0       1       0   
2      0      0       0       0       0       0       0       1       0   
3      0      0       0       0       0       0       0       1       0   
4      0      0       0       0       0       0       0       1       0   

   MDC_18  MDC_19  MDC_2  MDC_20  MDC_21  MDC_22  MDC_23  MDC_24  MDC_25  \
0       0       0      0       0       0       0       0       0       0   
1       0       0      0       0       0       0       0       0       0   
2       0       0      0       0       0       0       0       0       0   
3       0       0      0       0       0       0       0       0       0   
4       0       0      0       0       0       0       0       0       0   

   MDC_3  MDC_4  MDC_5  MDC_6  MDC_7  MDC_8  MDC_9  
0      0      0      0      0      0      0      0  
1      0      0      0      0      0      0      0  
2      0      0      0      0      0      0      0  
3      0      0      0      0      0      0      0  
4      0      0      0      0      0      0      0

In [94]:
path_mdc_df = '../../../data/hcup/nis/all_year_combination/mdc.pickle'

In [95]:
pd.concat([target_df, df_mdc], axis = 1).to_pickle(path_mdc_df)

## One-hot encoding DRG

In [96]:
df_drg = pd.get_dummies(input_df_other['DRG'], prefix = 'DRG')

In [ ]:
df_drg = df_drg.drop(columns = 'DRG_-99')
#df_drg = df_drg.drop(columns = 'DRG_-1')

In [100]:
path_drg_df = '../../../data/hcup/nis/all_year_combination/drg.pickle'

In [101]:
pd.concat([target_df, df_drg], axis = 1).to_pickle(path_drg_df)

## One-hot encoding YEAR

In [129]:
df_year = pd.get_dummies(fn_pt_trn.YEAR, prefix = 'YEAR')

In [130]:
df_year.head()

YEAR_2007  YEAR_2008  YEAR_2009  YEAR_2010  YEAR_2011  YEAR_2012  \
0          1          0          0          0          0          0   
1          1          0          0          0          0          0   
2          1          0          0          0          0          0   
3          1          0          0          0          0          0   
4          1          0          0          0          0          0   

   YEAR_2013  YEAR_2014  YEAR_2015  
0          0          0          0  
1          0          0          0  
2          0          0          0  
3          0          0          0  
4          0          0          0

## Create season variables

In [104]:
def aseason_spring(row):
    if row['AMONTH_3'] or row['AMONTH_4'] or row['AMONTH_5']:
        return 1
    else:
        return 0
def aseason_summer(row):
    if row['AMONTH_6'] or row['AMONTH_7'] or row['AMONTH_8']:
        return 1
    else:
        return 0
def aseason_fall(row):
    if row['AMONTH_9'] or row['AMONTH_10'] or row['AMONTH_11']:
        return 1
    else:
        return 0
def aseason_winter(row):
    if row['AMONTH_12'] or row['AMONTH_1'] or row['AMONTH_2']:
        return 1
    else:
        return 0

In [105]:
fn_pt_trn['ASEASON_SPRING'] = fn_pt_trn.apply(lambda row: aseason_spring(row),axis=1)
fn_pt_trn['ASEASON_SUMMER'] = fn_pt_trn.apply(lambda row: aseason_summer(row),axis=1)
fn_pt_trn['ASEASON_FALL'] = fn_pt_trn.apply(lambda row: aseason_fall(row),axis=1)
fn_pt_trn['ASEASON_WINTER'] = fn_pt_trn.apply(lambda row: aseason_winter(row),axis=1)

In [106]:
season_df = fn_pt_trn[['ASEASON_SPRING', 'ASEASON_SUMMER', 'ASEASON_FALL', 'ASEASON_WINTER']]

## Variable Groups Concatination

In [107]:
len(input_df_other)

126013

In [108]:
len(dx_df)

126013

In [109]:
len(pclass_df)

126013

In [110]:
len(pr_df)

126013

In [131]:
full_input_df = pd.concat([input_df_other, season_df, df_drg, df_mdc, dx_df, pclass_df, pr_df, dxccs_df, prccs_df, target_df, df_year, aprdrg_df], axis = 1)

In [132]:
full_input_df.head()

MDC  DRG CM_LYMPH CM_LIVER CM_PARA CM_RENLFAIL CM_AIDS CM_ALCOHOL  \
0  16  810        0        0       0           0       0          0   
1  16  574        0        0       0           0       0          0   
2  16  574        0        0       0           0       0          0   
3  16  574        0        0       0           0       0          0   
4  16  574        1        0       0           0       0          0   

  CM_ANEMDEF CM_ARTH CM_BLDLOSS CM_CHF CM_CHRNLUNG CM_COAG CM_DEPRESS CM_DM  \
0          0       0          0      0           0       0          0     0   
1          0       0          0      0           0       0          1     0   
2          0       0          0      0           0       0          0     0   
3          0       0          0      0           0       0          0     0   
4          0       0          0      0           0       0          0     0   

  CM_DMCX CM_DRUG CM_HTN_C CM_HYPOTHY CM_LYTES CM_METS CM_OBESE CM_NEURO  \
0       0       0        0          0        0       0        0        0   
1       0       0        0          0        0       0        0        0   
2       0       0        0          1        1       0        0        0   
3       0       0        0          0        0       0        0        0   
4       0       0        1          0        0       0        0        0   

  CM_PERIVASC CM_PSYCH CM_PULMCIRC CM_ULCER CM_VALVE CM_WGHTLOSS CM_TUMOR CCI  \
0           0        0           0        0        0           0        1   2   
1           0        0           0        0        0           0        1   2   
2           0        0           0        0        0           0        1   2   
3           0        0           0        0        0           0        1   2   
4           0        0           0        0        0           0        0   2   

   AMONTH_1  AMONTH_2  AMONTH_3  AMONTH_4  AMONTH_5  AMONTH_6  AMONTH_7  \
0         0         0         0         0         0         0         0   
1         1         0         0         0         0         0         0   
2         0         1         0         0         0         0         0   
3         0         0         1         0         0         0         0   
4         0         0         1         0         0         0         0   

   AMONTH_8  AMONTH_9  AMONTH_10  AMONTH_11  AMONTH_12  DQTR_1  DQTR_2  \
0         0         0          1          0          0       0       0   
1         0         0          0          0          0       1       0   
2         0         0          0          0          0       1       0   
3         0         0          0          0          0       1       0   
4         0         0          0          0          0       1       0   

   DQTR_3  DQTR_4  HOSP_REGION_1  HOSP_REGION_2  HOSP_REGION_3  HOSP_REGION_4  \
0       0       1              0              0              0              1   
1       0       0              0              0              0              1   
2       0       0              0              0              0              1   
3       0       0              0              0              0              1   
4       0       0              0              0              0              1   

   H_CONTRL_1  H_CONTRL_2  H_CONTRL_3  PAY1_1  PAY1_2  PAY1_3  PAY1_4  PAY1_5  \
0           0           1           0       0       0       1       0       0   
1           0           0           0       1       0       0       0       0   
2           0           1           0       0       0       1       0       0   
3           0           1           0       0       0       1       0       0   
4           0           0           0       1       0       0       0       0   

   PAY1_6  RACE_1  RACE_2  RACE_3  RACE_4  RACE_5  RACE_6 AWEEKEND ELECTIVE  \
0       0       1       0       0       0       0       0        1        0   
1       0       1       0       0       0       0       0        0        0   
2       0       1       0       0       0       0

In [133]:
full_input_df = full_input_df.convert_objects(convert_numeric=True)

/apps/python3/3.6.5/lib/python3.6/site-packages/ipykernel_launcher.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  """Entry point for launching an IPython kernel.


In [134]:
full_input_df.head()

MDC  DRG  CM_LYMPH  CM_LIVER  CM_PARA  CM_RENLFAIL  CM_AIDS  CM_ALCOHOL  \
0   16  810         0         0        0            0        0           0   
1   16  574         0         0        0            0        0           0   
2   16  574         0         0        0            0        0           0   
3   16  574         0         0        0            0        0           0   
4   16  574         1         0        0            0        0           0   

   CM_ANEMDEF  CM_ARTH  CM_BLDLOSS  CM_CHF  CM_CHRNLUNG  CM_COAG  CM_DEPRESS  \
0           0        0           0       0            0        0           0   
1           0        0           0       0            0        0           1   
2           0        0           0       0            0        0           0   
3           0        0           0       0            0        0           0   
4           0        0           0       0            0        0           0   

   CM_DM  CM_DMCX  CM_DRUG  CM_HTN_C  CM_HYPOTHY  CM_LYTES  CM_METS  CM_OBESE  \
0      0        0        0         0           0         0        0         0   
1      0        0        0         0           0         0        0         0   
2      0        0        0         0           1         1        0         0   
3      0        0        0         0           0         0        0         0   
4      0        0        0         1           0         0        0         0   

   CM_NEURO  CM_PERIVASC  CM_PSYCH  CM_PULMCIRC  CM_ULCER  CM_VALVE  \
0         0            0         0            0         0         0   
1         0            0         0            0         0         0   
2         0            0         0            0         0         0   
3         0            0         0            0         0         0   
4         0            0         0            0         0         0   

   CM_WGHTLOSS  CM_TUMOR  CCI  AMONTH_1  AMONTH_2  AMONTH_3  AMONTH_4  \
0            0         1    2         0         0         0         0   
1            0         1    2         1         0         0         0   
2            0         1    2         0         1         0         0   
3            0         1    2         0         0         1         0   
4            0         0    2         0         0         1         0   

   AMONTH_5  AMONTH_6  AMONTH_7  AMONTH_8  AMONTH_9  AMONTH_10  AMONTH_11  \
0         0         0         0         0         0          1          0   
1         0         0         0         0         0          0          0   
2         0         0         0         0         0          0          0   
3         0         0         0         0         0          0          0   
4         0         0         0         0         0          0          0   

   AMONTH_12  DQTR_1  DQTR_2  DQTR_3  DQTR_4  HOSP_REGION_1  HOSP_REGION_2  \
0          0       0       0       0       1              0              0   
1          0       1       0       0       0              0              0   
2          0       1       0       0       0              0              0   
3          0       1       0       0       0              0              0   
4          0       1       0       0       0              0              0   

   HOSP_REGION_3  HOSP_REGION_4  H_CONTRL_1  H_CONTRL_2  H_CONTRL_3  PAY1_1  \
0              0              1           0           1           0       0   
1              0              1           0           0           0       1   
2              0              1           0           1           0       0   
3              0              1           0           1           0       0   
4              0              1           0           0           0       1   

   PAY1_2  PAY1_3  PAY1_4  PAY1_5  PAY1_6  RACE_1  RACE_2  RACE_3  RACE_4  \
0       0       1       0       0       0       1       0       0       0   
1       0       0       0       0       0       1       0       0       0   
2       0       1       0       0       0       1       0     

In [135]:
full_input_df.to_pickle('/ufrc/djlemas/xinsongdu/jupyter_notebook/data/hcup/nis/all_year_combination/cleaned_for_repcv.pickle')